## Reference Videos

In [ ]:
# https://www.youtube.com/watch?v=o-pZk5R0TZg

## Imports

In [3]:
#  sentence_transformers import SentenceTransformer, InputExample, losses
from torch.utils.data import DataLoader
from sklearn.metrics import classification_report
from sklearn.metrics.pairwise import cosine_similarity
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
import logging
logging.basicConfig(format='%(asctime)s - %(message)s', level=logging.INFO)

## Import the data, as well as split into a smaller/larger dataset 

In [4]:
# Load datasets
df_examples = pd.read_parquet('shopping_queries_dataset_examples.parquet')
df_products = pd.read_parquet('shopping_queries_dataset_products.parquet')
df_sources = pd.read_csv('shopping_queries_dataset_sources.csv')

In [5]:
# Merge examples with products
df_examples_products = pd.merge(
    df_examples,
    df_products,
    how='left',
    left_on=['product_locale', 'product_id'],
    right_on=['product_locale', 'product_id']
)

# Task 1: Small version (filtered to U.S. locale and non-null titles)
df_task_1 = df_examples_products[
    (df_examples_products["small_version"] == 1) &
    (df_examples_products["product_locale"] == "us") &
    (df_examples_products["product_title"].notnull())
]

# Task 2: Large version
df_task_2 = df_examples_products[df_examples_products["large_version"] == 1]
df_task_2_train = df_task_2[df_task_2["split"] == "train"]
df_task_2_test = df_task_2[df_task_2["split"] == "test"]


## Initial Model: Smaller sample set, only looking at exact matches and using product titles
Scores: REALLY BAD

In [6]:
# Filter to Task 1 Train Set with Relevant (E) Labels
df_task_1_copy = df_task_1[
    (df_task_1["split"] == "train") &
    (df_task_1["esci_label"] == "E")
]

# Sample smaller set if needed (optional)
sample_df = df_task_1_copy.copy()

# Extract queries and product titles
queries = sample_df['query'].astype(str).values
products = sample_df['product_title'].astype(str).values

# TF-IDF Vectorizer on combined
vectorizer = TfidfVectorizer()
query_vecs = vectorizer.fit_transform(queries)
product_vecs = vectorizer.transform(products)  # Use same vocab

# Score and Recommend Top 3 Products per Query
for i, query in enumerate(queries):
    scores = cosine_similarity(query_vecs[i], product_vecs).flatten()
    ranked_indices = scores.argsort()[::-1]
    
    print(f"\nTop matches for: '{query}'")
    for idx in ranked_indices[:3]:
        print(f"- {products[idx]} (score: {scores[idx]:.4f})")


Top matches for: '!awnmower tires without rims'
- 17x7 Enkei EKM3 (Gunmetal) Wheels/Rims 5x100 (442-770-8045GM) (score: 0.4192)
- TDPRO 4PCS 145/70-6 Tires With 6 inch Wheels Rims for ATV Go Kart (score: 0.3681)
- Enkei 17x7 EDR9 (Matte Black) Wheels/Rims 5x100/114.3 (441-770-0245BK) (score: 0.3153)

Top matches for: '!awnmower tires without rims'
- 17x7 Enkei EKM3 (Gunmetal) Wheels/Rims 5x100 (442-770-8045GM) (score: 0.4192)
- TDPRO 4PCS 145/70-6 Tires With 6 inch Wheels Rims for ATV Go Kart (score: 0.3681)
- Enkei 17x7 EDR9 (Matte Black) Wheels/Rims 5x100/114.3 (441-770-0245BK) (score: 0.3153)

Top matches for: '!awnmower tires without rims'
- 17x7 Enkei EKM3 (Gunmetal) Wheels/Rims 5x100 (442-770-8045GM) (score: 0.4192)
- TDPRO 4PCS 145/70-6 Tires With 6 inch Wheels Rims for ATV Go Kart (score: 0.3681)
- Enkei 17x7 EDR9 (Matte Black) Wheels/Rims 5x100/114.3 (441-770-0245BK) (score: 0.3153)

Top matches for: '!awnmower tires without rims'
- 17x7 Enkei EKM3 (Gunmetal) Wheels/Rims 5x10


Top matches for: '# 10 self-seal envelopes without window'
- Self Seal Double Window Security Envelopes (#10 - Box of 500), for Invoices, Statements and Legal Documents (4 1/8" x 9 1/2") (score: 0.6234)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business Statements, Quickbooks Invoices, and Return Envelopes 4 1/8 X 9 ½’’ (score: 0.6204)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business Statements, Quickbooks Invoices, and Return Envelopes 4 1/8 X 9 ½’’ (score: 0.6204)

Top matches for: '# 10 self-seal envelopes without window'
- Self Seal Double Window Security Envelopes (#10 - Box of 500), for Invoices, Statements and Legal Documents (4 1/8" x 9 1/2") (score: 0.6234)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business Statements, Quickbooks Invoices, and Return Envelopes 4 1/8 X 9 ½’’ (score: 0.6204)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for B


Top matches for: '# 2 pencils not sharpened'
- Wood-Cased #2 HB Pencils, Yellow, Pre-sharpened, Class Pack, 320 pencils (score: 0.6606)
- Wood-Cased #2 HB Pencils, Yellow, Pre-sharpened, Class Pack, 1000 pencils (score: 0.6606)
- Madisi Golf Pencils with Eraser, 2 HB Half Pencils, 3.5" Mini Pencils, Pre-Sharpened, colorful pencils, 96 Count (score: 0.6481)

Top matches for: '# 2 pencils not sharpened'
- Wood-Cased #2 HB Pencils, Yellow, Pre-sharpened, Class Pack, 320 pencils (score: 0.6606)
- Wood-Cased #2 HB Pencils, Yellow, Pre-sharpened, Class Pack, 1000 pencils (score: 0.6606)
- Madisi Golf Pencils with Eraser, 2 HB Half Pencils, 3.5" Mini Pencils, Pre-Sharpened, colorful pencils, 96 Count (score: 0.6481)

Top matches for: '# 2 pencils not sharpened'
- Wood-Cased #2 HB Pencils, Yellow, Pre-sharpened, Class Pack, 320 pencils (score: 0.6606)
- Wood-Cased #2 HB Pencils, Yellow, Pre-sharpened, Class Pack, 1000 pencils (score: 0.6606)
- Madisi Golf Pencils with Eraser, 2 HB Half Pencil


Top matches for: '#1 best and not expensive bath back brush cream color'
- LFJ 3 in 1 Back Bath Brush Set for Shower, 19" Long Handle Body Brush, Bath Sponge and Pumice Gentle Exfoliation and Improved Skin Health, Suitable for Men and Women (score: 0.4026)
- 131704 Cement Color (score: 0.3422)
- Baxter's Back! (score: 0.3334)

Top matches for: '#1 best and not expensive bath back brush cream color'
- LFJ 3 in 1 Back Bath Brush Set for Shower, 19" Long Handle Body Brush, Bath Sponge and Pumice Gentle Exfoliation and Improved Skin Health, Suitable for Men and Women (score: 0.4026)
- 131704 Cement Color (score: 0.3422)
- Baxter's Back! (score: 0.3334)

Top matches for: '#1 best and not expensive bath back brush cream color'
- LFJ 3 in 1 Back Bath Brush Set for Shower, 19" Long Handle Body Brush, Bath Sponge and Pumice Gentle Exfoliation and Improved Skin Health, Suitable for Men and Women (score: 0.4026)
- 131704 Cement Color (score: 0.3422)
- Baxter's Back! (score: 0.3334)

Top matches 


Top matches for: '#10 window envelopes not self seal'
- Self Seal Double Window Security Envelopes (#10 - Box of 500), for Invoices, Statements and Legal Documents (4 1/8" x 9 1/2") (score: 0.6113)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business Statements, Quickbooks Invoices, and Return Envelopes 4 1/8 X 9 ½’’ (score: 0.6084)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business Statements, Quickbooks Invoices, and Return Envelopes 4 1/8 X 9 ½’’ (score: 0.6084)

Top matches for: '#10 window envelopes not self seal'
- Self Seal Double Window Security Envelopes (#10 - Box of 500), for Invoices, Statements and Legal Documents (4 1/8" x 9 1/2") (score: 0.6113)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business Statements, Quickbooks Invoices, and Return Envelopes 4 1/8 X 9 ½’’ (score: 0.6084)
- Office Deed 500 #10 Self Seal Double Window Security Envelopes-Designed for Business St

...


Top matches for: '15 mexican dress'
- Campesino black mexican dress for 15-18 years old woman (score: 0.6310)
- Mexican Reboso accesory Mexican Fiesta (score: 0.6180)
- Campesino white mexican dress with sleeves for 15-18 years old woman (score: 0.5750)

Top matches for: '15 mexican dress'
- Campesino black mexican dress for 15-18 years old woman (score: 0.6310)
- Mexican Reboso accesory Mexican Fiesta (score: 0.6180)
- Campesino white mexican dress with sleeves for 15-18 years old woman (score: 0.5750)

Top matches for: '15 mexican dress'
- Campesino black mexican dress for 15-18 years old woman (score: 0.6310)
- Mexican Reboso accesory Mexican Fiesta (score: 0.6180)
- Campesino white mexican dress with sleeves for 15-18 years old woman (score: 0.5750)

Top matches for: '15 mexican dress'
- Campesino black mexican dress for 15-18 years old woman (score: 0.6310)
- Mexican Reboso accesory Mexican Fiesta (score: 0.6180)
- Campesino white mexican dress with sleeves for 15-18 years old wo


Top matches for: '15 month montessori'
- Keyboard Skins Compatible for 15.6" HP Pavilion 15-ab 15-ac 15-ae 15-af 15-an 15-ak 15-as 15-au 15-ay 15-ba 15-bc 15-bk Series, HP Envy x360 m6-ae151dx m6-p113dx m6-w, HP OMEN 15-ax (Ombre Mint Blue) (score: 0.4298)
- mCover Hard Shell Case for 15.6" HP Pavilion 15-CSxxxx (15-CS0000 to 15-CS9999) Series (NOT Fitting 15-AY / 15-BA / 15-AU / 15-CC / 15-BS etc or Envy Series laptops) Notebook PC (Pink) (score: 0.4267)
- Keyboard Cover for 15.6" HP Pavilion 15-b 15-d 15-e 15-f 15-g 15-j 15-k 15-n 15-p 15-r 15-u m6-k m6-n, 17.3" Envy 17-j 17t-j 17-e m7-j - Compatible Models Listed in Product Description, Black (score: 0.4231)

Top matches for: '15 month montessori'
- Keyboard Skins Compatible for 15.6" HP Pavilion 15-ab 15-ac 15-ae 15-af 15-an 15-ak 15-as 15-au 15-ay 15-ba 15-bc 15-bk Series, HP Envy x360 m6-ae151dx m6-p113dx m6-w, HP OMEN 15-ax (Ombre Mint Blue) (score: 0.4298)
- mCover Hard Shell Case for 15.6" HP Pavilion 15-CSxxxx (15-CS0000 to 


Top matches for: '150 watt high pressure sodium light fixture'
- Sunlite 04947-SU WPM150HPS 150 Watt High Pressure Sodium Medium Wall Pack Fixture (score: 0.8525)
- High Yield Lighting FloraLux 150-Watt High Pressure Sodium (HPS) Complete Grow Light, Bulb Included (score: 0.6669)
- Hubbell Outdoor Lighting DDS-150S 150-Watt High Pressure Sodium Dusk-to-Dawn Kit (score: 0.6307)

Top matches for: '150 watt high pressure sodium light fixture'
- Sunlite 04947-SU WPM150HPS 150 Watt High Pressure Sodium Medium Wall Pack Fixture (score: 0.8525)
- High Yield Lighting FloraLux 150-Watt High Pressure Sodium (HPS) Complete Grow Light, Bulb Included (score: 0.6669)
- Hubbell Outdoor Lighting DDS-150S 150-Watt High Pressure Sodium Dusk-to-Dawn Kit (score: 0.6307)

Top matches for: '150 watt high pressure sodium light fixture'
- Sunlite 04947-SU WPM150HPS 150 Watt High Pressure Sodium Medium Wall Pack Fixture (score: 0.8525)
- High Yield Lighting FloraLux 150-Watt High Pressure Sodium (HPS) Complet


Top matches for: '15gal water container'
- Zulay Kitchen Bacon Grease Container With Strainer - 1L Stainless Steel Cooking Oil Container With Lid & Handle - Large Ghee Container or Bacon Fat Container Perfect For Storing Fats & Frying Oils (score: 0.3229)
- PANKIO Water Jug 2.2L Big Water Bottle 73OZ Half Gallon Sports Water Bottle Big Capacity Container BPA Free Water Bottles for Fitness Gym Yoga Travel Cycling Camping Outdoor (score: 0.3107)
- Scepter 05935 Military Water Container - 5 Gallon (20 Litre), AM Sand (score: 0.3107)

Top matches for: '15gal water container'
- Zulay Kitchen Bacon Grease Container With Strainer - 1L Stainless Steel Cooking Oil Container With Lid & Handle - Large Ghee Container or Bacon Fat Container Perfect For Storing Fats & Frying Oils (score: 0.3229)
- PANKIO Water Jug 2.2L Big Water Bottle 73OZ Half Gallon Sports Water Bottle Big Capacity Container BPA Free Water Bottles for Fitness Gym Yoga Travel Cycling Camping Outdoor (score: 0.3107)
- Scepter 0593

KeyboardInterrupt: 

In [7]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

# Filter to Task 1 Train Set with Relevant (E) Labels
df_task_1_copy = df_task_1[
    (df_task_1["split"] == "train") &
    (df_task_1["esci_label"] == "E")
].copy()

# Fill missing values and combine product metadata (for retrieval)
df_task_1_copy['product_title'] = df_task_1_copy['product_title'].fillna('')
df_task_1_copy['product_description'] = df_task_1_copy['product_description'].fillna('')
df_task_1_copy['product_brand'] = df_task_1_copy['product_brand'].fillna('')
df_task_1_copy['product_bullet_point'] = df_task_1_copy['product_bullet_point'].fillna('')

df_task_1_copy['full_product_text'] = (
    df_task_1_copy['product_title'] + ' ' +
    df_task_1_copy['product_description'] + ' ' +
    df_task_1_copy['product_brand'] + ' ' +
    df_task_1_copy['product_bullet_point']
)

sample_df = df_task_1_copy.sample(n=10000, random_state=42).copy()

# Extract queries and product titles for display
queries = sample_df['query'].astype(str).tolist()
product_texts = sample_df['full_product_text'].astype(str).tolist()
product_titles = sample_df['product_title'].astype(str).tolist()

# TF-IDF Vectorizer
vectorizer = TfidfVectorizer()
query_vecs = vectorizer.fit_transform(queries)
product_vecs = vectorizer.transform(product_texts)

# Score and Recommend Top 3 Product Titles per Query
for i, query in enumerate(queries):
    scores = cosine_similarity(query_vecs[i], product_vecs).flatten()
    ranked_indices = scores.argsort()[::-1]
    
    print(f"\nTop matches for: '{query}'")
    for idx in ranked_indices[:3]:
        print(f"- {product_titles[idx]} (score: {scores[idx]:.4f})")



Top matches for: 'drainer for sink'
- Rubbermaid 6008ARBLK Black Chrome Twin Sink Dish Drainer (score: 0.5217)
- Kitchen Sink Undermount Double Bowl - Lordear 32 inch Undermount Sink 16 Gauge Stainless Steel Round Corner Double Bowl 60/40 Kitchen Sink Basin (score: 0.2962)
- Stylish Sturdy Oil Rubbed Bronze Metal Wire Small Dish Drainer Drying Rack (score: 0.2747)

Top matches for: 'chernobyl'
- Azure Dust: Inside Chernobyl's Exclusion Zone (score: 0.5283)
- Purina Beneful Real Meat Dry Dog Food, Originals With Farm-Raised Beef - (4) 3.5 lb. Bags (score: 0.0000)
- BLUE PANDA Hello 21 Cake Topper and Thin Candles in Holders (Rose Gold, 31 Pieces) (score: 0.0000)

Top matches for: 'retaine eye drops for dry eyes preservative free'
- UrsaPharm Hylo-Forte Lubricating Eye Drops 10Ml - Pack of 2 (score: 0.4493)
- LUMIFY Redness Reliever Eye Drops 0.25 Ounce (7.5mL) (score: 0.4262)
- Red Eyes / Crazyface [Explicit] (score: 0.3114)

Top matches for: 'long sleeve pink dress'
- vermers Bathrobe


Top matches for: 'midevil accessories'
- Zinc Alloy Filter Hookah Hose, JUMEIGE New Shisha Set, Shisha Gift Accessories for Filtration of Hazardous Substances (Golden) (score: 0.1809)
- Xvevina Vintage Gold Red Rhinestones Deco Venetian Masquerade Mask Women Accessories Favor (score: 0.1750)
- Dreamgirl Women's Lieutenant Ivana Misbehave Costume, Blue, Small (score: 0.1659)

Top matches for: 'jump rope without the rope'
- Redify Weighted Cordless Jump Rope for Fitness [Suitable for Different Ages and Levels] Ropeless Jump Rope for Crossfit Boxing MMA WOD Training, High Speed Rope Skipping for Narrow Space (Blue) (score: 0.6711)
- WOW World of Watersports 4k 60 ft. Tow Rope with Floating Foam Buoy 1 2 3 or 4 Person Tow Rope for Boating, 11-3010 (score: 0.5304)
- Castaway Living 13 ft. Double Traditional Hand Woven Cotton Rope Hammock with Free Extension Chains & Tree Hooks, Designed in The USA, Accommodates Two People with a Weight Capacity of 450 lbs. (score: 0.4874)

Top matches for:


Top matches for: '4ff to 3ff adapter'
- 3 Prong to 2 Prong Adapter, 2 Pack, LENCENT 3 Outlets Extender with 3 USB Ports, Wall Charger, Multi Plug Extender Splitter, Travel Adaptor for US to Japan Philippines-Type A, Cruise Ship Approved (score: 0.2526)
- USB C Male to USB 3.0 Female Adapter 3-Pack,Thunderbolt 3 to Type A OTG Cable Converter for MacBook Pro,iPad Air 4 4th Mini 6 6th Generation,S21,21,Microsoft Surface Go,Galaxy Note 20 S20 Plus Ultra (score: 0.2417)
- LAPUTA SSD Convert Card, M.2 NVME SSD Convert Card Adapter Compatible with MacBook Ai-r 11inch A1465 Pro Retina 13inch (score: 0.2398)

Top matches for: '4" round rv interior led light'
- CARLITS Eagle Eye LED Bulbs 10-Pack Ultra thin Bumper DRL Fog Lights Motorcycle Light Daytime Running DRL Tail Backup Light Car Motor Marker Lights LED 12V (Black Case, Red) (score: 0.3020)
- Brahmin Duxbury Satchel Convertible Top Handle Bag, Pecan, One Size (score: 0.2751)
- Tenergy LED Candelabra Bulbs Dimmable, 4W (40 Watt Equivalent


Top matches for: 'low dome disposable cake boxes'
- 43 Pieces Sunflower Cake Topper Sunflower Cupcake Toppers Sunflower Birthday Party Decorations Sun Flower Cake Picks Yellow Daisy Cupcake Topper for Girl Boys Baby Shower Supplies Decor (score: 0.2046)
- uBoxes Large Moving Boxes 20" x 20" x 15" (Pack of 6) (score: 0.2019)
- Katgely 10 Inch Plastic Pie Containers With Low Dome (Pack of 20) (score: 0.2005)

Top matches for: 'cervical peanut'
- PBfit All-Natural Peanut Butter Powder 15 Ounce, Peanut Butter Powder from Real Roasted Pressed Peanuts, Low in Fat High in Protein, Natural Ingredients (score: 0.2952)
- Robert Irvine's Fitcrunch Chocolate Peanut Butter, 18 ct. -2 Packs (score: 0.2833)
- KIND Nut Butter Bars, Chocolate Peanut Butter, 1.3 Ounce, 32 Count, Gluten Free, 100% Whole Grains (score: 0.2504)

Top matches for: 'resin planters'
- Epoxy Resin Kit Liquid Glass Epoxy Resin Molds Silicone Kit Bundle | Pixiss Easy Mix 1:1 (17-Ounce Kit) | Epoxy Resin Mixing Cups and Supplies 


Top matches for: 'storm crux bowling ball'
- Storm Crux Prime 15lbs (score: 0.4200)
- This Storm: A novel (score: 0.3212)
- Born in the Storm (score: 0.3081)

Top matches for: 'weed wacker with metal blade'
- Agfabric Woven Weed Barrier 6'x300',3.0oz (score: 0.3854)
- Stanley Hand Tools 10-499 Retractable Blade Quick-Change Utility Knife (score: 0.3201)
- GALAX PRO Reciprocating Saw, Cordless Reciprocating Saw with Fast Charger, Tool-free Blade Change and Variable Speed, 3pcs 6-inch Wood Saw Blade & 2pcs 6-inch Metal Saw Blade (score: 0.2837)

Top matches for: 'cooks essentials air fryer'
- The Skinnytaste Air Fryer Cookbook: The 75 Best Healthy Recipes for Your Air Fryer (score: 0.4348)
- Instant Pot Air Fryer Lid 6 in 1, No Pressure Cooking Functionality, 6 Qt, 1500 W (score: 0.3202)
- The Essential Air Fryer Cookbook for Two: Perfectly Portioned Recipes for Healthier Fried Favorites (score: 0.2799)

Top matches for: 'thomas train wooden cars'
- Cruel Train (score: 0.5224)
- Thomas 

...


Top matches for: 'ratchet belts for men without buckle'
- Vatee's Women's/Men's Real Leather Replacement Belt Strap No Buckle 1 1/2"(38mm) Wide 45" Long Black (score: 0.3477)
- Vatee's Women's Reversible Real Leather Replacement Belt Strap without Buckle 1"/25mm Wide Adjustable 37" Long White/Black (score: 0.3241)
- Men's Leather Ratchet Belt Strap Multiple Colour Without Buckle 35mm 1.38 inches Wide (score: 0.2851)

Top matches for: 'yeti tall thin can cooler'
- Lifewit Cooler Backpack Leakrproof 32 Can Insulated Lightweight Backpack Cooler, Large Capacity Soft-Sided Double Decker Cooler Bag for Men Women to Beach/Picnic/Camping/Hiking/Day Trips (score: 0.3377)
- YETI Rambler 16 oz. Colster Tall Can Insulator for Tallboys & 16 oz. Cans, Stainless (score: 0.2823)
- NCAA LSU Tigers Trash Can Cooler (score: 0.2221)

Top matches for: 'uin shoes women'
- Penny Loafer for Women - Low Heels Casual Daily Shoe Moccasins Slip-Ons Ladies Dress Pumps Shoes (score: 0.4017)
- Boys Girls Kids Rain 


Top matches for: 'rv caulking sealant'
- Dicor 501LSW-1, RV Rubber Roof Sealant Self Leveling Caulk, White, 4 Pack (score: 0.3449)
- Durevole RV Repair Caulking Self-Leveling Lap Sealant Instrallation Kit - Sealants, Butyl Tapes, Screws - White (score: 0.3070)
- FROTH-PAK 12, Spray Foam Sealant Kits, 12 board feet/kit - 2 Complete Kits (score: 0.2227)

Top matches for: 'plastic file holders'
- IRIS USA Letter & Legal Size Plastic Storage Bin Tote Organizing File Box with Durable and Secure Latching Lid, Stackable and Nestable, 4 Pack, Black (score: 0.2889)
- Pendaflex Portable Desktop File, Side Handles, Hanging File Folders, Tabs & Inserts, Letter Size, 9-1/2 x 12-3/16 x 6 Inches, Black (23013) (score: 0.2412)
- Rosé All Day Plastic Tablecloths, 3 ct (score: 0.2132)

Top matches for: 'resident aliens'
- Resident Aliens: Life in the Christian Colony by Stanley Hauerwas, William H. Willimon (1989) Paperback (score: 0.4830)
- RESIDENT ALIEN by Quentin Crisp (2008-07-01) (score: 0.3162)



Top matches for: 'forearm sleeve'
- vermers Bathrobe Hooded Men - Men's Long Hooded Shawl Bathrobe Home Clothes Lightweight Robe(5XL, Red) (score: 0.3096)
- Champion Men's Classic Jersey TEE, Cargo Olive, X Large (score: 0.2726)
- onlypuff Tie Dye Hoodies for Women Ombre Long Sleeve Shirts Gray Sweatshrit Tunics for Leggings L (score: 0.2537)

Top matches for: '+3/4 sleeve for women not plus'
- FRC0LT Hoodies, Womens Kawaii Clouds Printing Long Sleeve Casual Sweatshirt Pullover (L, White Cloud) (score: 0.3893)
- vermers Bathrobe Hooded Men - Men's Long Hooded Shawl Bathrobe Home Clothes Lightweight Robe(5XL, Red) (score: 0.3785)
- Nemidor Women's V-Neckline Stretchy Casual Midi Plus Size Bridesmaid Dress (20W, Darkpurple) (score: 0.3689)

Top matches for: 'uv airtight glass jar'
- Herb Guard - 1 Oz Airtight Jar and Smell Proof Container (500 ml) Comes with Humidity Pack to Keep Goods Fresh for Months (score: 0.3046)
- Green Protected Airtight Herb Container - Quad Oz Smell Proof Glass


Top matches for: 'foodsaver'
- FoodSaver Vacuum Sealer Machine with Starter Vacuum Seal Bags & Rolls, Safety Certified, Black - FM2000-FFP (score: 0.1788)
- FoodSaver V4400 2-in-1 Vacuum Sealer Machine with Automatic Vacuum Sealer Bag Detection and Starter Kit, Safety Certified, Black and Silver (score: 0.1769)
- 100 Pint Vacuum Sealer Storage Bags 6 x 10 Inch Size for Food Saver, Seal a Meal Sealers, BPA Free, Heavy Duty Commercial Grade, Sous Vide Vaccume Meal Safe, Universal Pre-Cut Bag Design Avid Armor (score: 0.0381)

Top matches for: 'footed blankets'
- Newborn Baby Girl Boy Footie Sleeper Pajamas Ruffle Romper Jumpsuit Knitted Outfits Clothes (B-Purple, 3-6 Months) (score: 0.2614)
- Luvable Friends Unisex Baby Cotton Flannel Receiving Blankets, Pink Dots, One Size (score: 0.2079)
- Rene Rofe Ladies Sleepwear One-Piece Holiday Micro-Fleece Footed Onesie Sleeper Pajama (Indigo Bunnies, Large) (score: 0.2057)

Top matches for: 'mamba shurt'
- Mamba Original 0.5 Gram 40mm Electric


Top matches for: '1.5 mortise cylinder'
- Baldwin 8325.003 Mortise Lock Cylinder 1-1/2" Diameter, Lifetime Brass (score: 0.3784)
- Baldwin 8325 1-1/2" Mortise Cylinder C Keyway, Lifetime Satin Nickel (score: 0.3331)
- LawnMowerParts V100000260 Genuine Echo/Shindaiwa Cylinder Gasket PB-500H PB-500T EB508RT (score: 0.2729)

Top matches for: 'babys first bottle warmer'
- Bottle Warmer, Baby Bottle Warmer, Fast Breast Milk Warmer with a Timer, Baby Food Heater with LCD Display, Accurate Temperature Control, Constant Mode, Fit All Baby Bottles (score: 0.3006)
- Baby Bottle Warmer, Chefhandy Multifunctional Baby Bottle Warmer and Food Heater with LCD Display, Precise Temperature Control, Fast Warmer for Baby Milk and Formula (score: 0.2993)
- First Look, Season 14 (score: 0.2768)

Top matches for: 'dust mite'
- POWERTEC 70198 2-1/2-Inch Flexible Dust Collection Hose 36-Inch Long, black, 2-1/2-Inch (score: 0.3195)
- Azure Dust: Inside Chernobyl's Exclusion Zone (score: 0.3142)
- Five-Layer A

## Incorporate Sentence Transformers (this library literally not working for me and I've been trying to fix for two hours lol. Going to leave this in as a model that would've been great if it worked)

In [8]:
import pandas as pd
import numpy as np
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity

# Sample 20 rows from Task 1 (you can adjust this as needed)
sample_df = df_task_1.sample(n=20, random_state=42).copy()

# Ensure bullet point and other fields exist
sample_df['product_bullet_point'] = sample_df.get('product_bullet_point', '').fillna('')
sample_df['product_description'] = sample_df['product_description'].fillna('')
sample_df['product_brand'] = sample_df['product_brand'].fillna('')
sample_df['product_title'] = sample_df['product_title'].fillna('')

# Combine metadata into a single product string
sample_df['full_product_text'] = (
    sample_df['product_title'] + ' ' +
    sample_df['product_description'] + ' ' +
    sample_df['product_brand'] + ' ' +
    sample_df['product_bullet_point']
)

# Prepare text for encoding
queries = sample_df['query'].astype(str).tolist()
products = sample_df['full_product_text'].astype(str).tolist()

# Load sentence-transformer model
model = SentenceTransformer('all-MiniLM-L6-v2')

# Compute embeddings
query_vecs = model.encode(queries, convert_to_numpy=True)
product_vecs = model.encode(products, convert_to_numpy=True)

# Compute similarity and print top matches
for i, query in enumerate(queries):
    scores = cosine_similarity(query_vecs[i].reshape(1, -1), product_vecs).flatten()
    
    # Normalize scores
    scores = (scores - scores.min()) / (scores.max() - scores.min() + 1e-8)
    ranked_indices = scores.argsort()[::-1]
    
    print(f"\nTop matches for: '{query}'")
    for idx in ranked_indices[:3]:
        title = sample_df.iloc[idx]['product_title']
        print(f"- {title} (score: {scores[idx]:.4f})")


/Users/sarahpopeck/anaconda3/lib/python3.11/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
2025-07-20 15:40:28,367 - Use pytorch device_name: mps
2025-07-20 15:40:28,369 - Load pretrained SentenceTransformer: all-MiniLM-L6-v2
/Users/sarahpopeck/anaconda3/lib/python3.11/site-packages/huggingface_hub/file_download.py:943: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]


Top matches for: 'woman penny loafers shoes'
- Sperry Women's Seaport Penny Tri Tone Loafer, Tan/White, 9 (score: 1.0000)
- Breadman 2 lb Professional Bread Maker, Stainless Steel, BK1050S (score: 0.5949)
- Book Ends, Bookends, Book Ends for Shelves, Bookends for Heavy Books, Book Divider Decorative Holder, Metal Heavy Duty Bookend Black 1 Pair, Abstract Art Desgin Book Stopper Supports for Office, Home (score: 0.4822)

Top matches for: 'retaine eye drops for dry eyes preservative free'
- Systane Long Lasting Lubricant Eye Drops Vials Eye Drops, 30 Count, 0.7 ml (Pack of 1) (score: 1.0000)
- Naturel Promise Fresh Dental Water Additive - Dental Health Solution for Dogs - Easy to Use - Helps Clean Teeth - Freshens Breath Up to 12 Hours - No Brushing Required - 18 Fl Oz, 3 Pack (score: 0.4838)
- Sun Kissed Tanning Pills Tan Fast Fake Tanning Pill! Instant Tan No Sun! Try Now (score: 0.4719)

Top matches for: 'jamie oliver veg'
- Martin Furniture Storage Credenza, Brown (score: 1.0000)
- 

## Incorporate training and test

In [ ]:
import pandas as pd
import numpy as np
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity

train_df = df_task_1[df_task_1["split"] == "train"]
train_df['product_title'] = train_df['product_title'].fillna('')
train_df['product_description'] = train_df['product_description'].fillna('')
train_df['product_brand'] = train_df['product_brand'].fillna('')
train_df['product_bullet_point'] = train_df.get('product_bullet_point', '').fillna('')

train_df['full_product_text'] = (
    train_df['product_title'] + ' ' +
    train_df['product_description'] + ' ' +
    train_df['product_brand'] + ' ' +
    train_df['product_bullet_point']
)
df_task_1_test = df_task_1[df_task_1["split"] == "test"]

train_products = train_df['full_product_text'].astype(str).tolist()
train_titles = train_df['product_title'].astype(str).tolist()  # for display

# Prepare test queries
test_df = df_task_1_test.sample(n=5, random_state=24).copy()
test_queries = test_df['query'].astype(str).tolist()

# Load the model and compute embeddings
model = SentenceTransformer('all-MiniLM-L6-v2')
product_vecs = model.encode(train_products, convert_to_numpy=True)
query_vecs = model.encode(test_queries, convert_to_numpy=True)

# Recommend top-3 products for each test query
for i, query in enumerate(test_queries):
    scores = cosine_similarity(query_vecs[i].reshape(1, -1), product_vecs).flatten()
    
    # Normalize scores between 0 and 1
    scores = (scores - scores.min()) / (scores.max() - scores.min() + 1e-8)
    ranked_indices = scores.argsort()[::-1]

    print(f"\nTop matches for test query: '{query}'")
    for idx in ranked_indices[:3]:
        print(f"- {train_titles[idx]} (score: {scores[idx]:.4f})")


/var/folders/qz/_plh__x56hj5r6twwvlby_rc0000gn/T/ipykernel_48582/765702799.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_df['product_title'] = train_df['product_title'].fillna('')
/var/folders/qz/_plh__x56hj5r6twwvlby_rc0000gn/T/ipykernel_48582/765702799.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_df['product_description'] = train_df['product_description'].fillna('')
/var/folders/qz/_plh__x56hj5r6twwvlby_rc0000gn/T/ipykernel_48582/765702799.py:9: SettingWithCopyWarning: 
A value is

Batches:   0%|          | 0/5682 [00:00<?, ?it/s]

## Trying to use Recall and MRR (This doesn't work)

In [ ]:
# === Filter for US, Exact Matches, Titles Present ===
df_task_1 = df[
    (df["small_version"] == 1) &
    (df["product_locale"] == "us") &
    (df["product_title"].notnull()) &
    (df["esci_label"] == "E")
]

# === Full Train and Test Sets ===
df_train = df_task_1[df_task_1["split"] == "train"].copy()
df_test = df_task_1[df_task_1["split"] == "test"].sample(n=20, random_state=24).copy()

# === Build full product metadata ===
df_train['full_product_text'] = (
    df_train['product_title'].fillna('') + ' ' +
    df_train['product_description'].fillna('') + ' ' +
    df_train['product_brand'].fillna('')
)

# === SentenceTransformer Embeddings ===
model = SentenceTransformer('all-MiniLM-L6-v2')
product_vecs = model.encode(df_train['full_product_text'].values, convert_to_tensor=True)
product_ids = df_train['product_id'].values

query_vecs = model.encode(df_test['query'].values, convert_to_tensor=True)
true_ids = df_test['product_id'].values

# === Evaluate Recall@3 and MRR@3 ===
k = 3
recall_hits = 0
reciprocal_ranks = []

for i in range(len(df_test)):
    scores = cosine_similarity(
        query_vecs[i].cpu().numpy().reshape(1, -1),
        product_vecs.cpu().numpy()
    ).flatten()

    ranked_indices = scores.argsort()[::-1][:k]
    retrieved_ids = product_ids[ranked_indices]

    print(f"\n🔍 Query: {df_test.iloc[i]['query']}")
    print("Top retrieved product IDs:", list(retrieved_ids))
    print("True product ID:", true_ids[i])

    if true_ids[i] in retrieved_ids:
        recall_hits += 1
        rank = list(retrieved_ids).index(true_ids[i]) + 1
        reciprocal_ranks.append(1.0 / rank)
    else:
        reciprocal_ranks.append(0.0)

recall_at_k = recall_hits / len(df_test)
mrr_at_k = np.mean(reciprocal_ranks)

print(f"\n✨ Evaluation Results (Full Train Set):")
print(f"Recall@{k}: {recall_at_k:.4f}")
print(f"MRR@{k}:    {mrr_at_k:.4f}")

## Avoids sentence transformer, but really bad scores

In [ ]:
import torch
from transformers import AutoTokenizer, AutoModel
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
import pandas as pd

# Load HF model + tokenizer
model_name = "sentence-transformers/all-MiniLM-L6-v2"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModel.from_pretrained(model_name)

# Mean pooling function
def mean_pooling(model_output, attention_mask):
    token_embeddings = model_output[0]  # first element of output: last hidden states
    input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size())
    return (token_embeddings * input_mask_expanded).sum(1) / input_mask_expanded.sum(1)

# Preprocess text → embeddings
def get_embeddings(texts):
    encoded_input = tokenizer(texts, padding=True, truncation=True, return_tensors='pt')
    with torch.no_grad():
        model_output = model(**encoded_input)
    return mean_pooling(model_output, encoded_input['attention_mask']).cpu().numpy()

# Your product data
df = df_task_1.sample(n=20, random_state=42).copy()
df['product_bullet_point'] = df['product_bullet_point'].fillna('')
df['product_description'] = df['product_description'].fillna('')
df['product_brand'] = df['product_brand'].fillna('')
df['product_title'] = df['product_title'].fillna('')

df['full_product_text'] = (
    df['product_title'] + ' ' +
    df['product_description'] + ' ' +
    df['product_brand'] + ' ' +
    df['product_bullet_point']
)

queries = df['query'].astype(str).tolist()
products = df['full_product_text'].astype(str).tolist()
titles = df['product_title'].astype(str).tolist()

# Embeddings
query_vecs = get_embeddings(queries)
product_vecs = get_embeddings(products)

# Matchmaking
for i, query in enumerate(queries):
    scores = cosine_similarity(query_vecs[i].reshape(1, -1), product_vecs).flatten()
    top_idxs = scores.argsort()[::-1][:3]
    
    print(f"\nTop matches for: '{query}'")
    for idx in top_idxs:
        print(f"- {titles[idx]} (score: {scores[idx]:.4f})")
